In [1]:
from web2json.preprocessor import *
from web2json.ai_extractor import *
from web2json.postprocessor import *
from web2json.pipeline import *

In [2]:
import dotenv
dotenv.load_dotenv()

True

In [3]:
llm = NvidiaLLMClient(config={'api_key': os.getenv('NVIDIA_API_KEY'),'model_name': 'qwen/qwen2.5-7b-instruct'})
reranker = NvidiaRerankerClient(config={'api_key': os.getenv('NVIDIA_API_KEY'),'model_name': 'nv-rerank-qa-mistral-4b:1'})
# reranker = HFRerankerClient()

In [4]:
prompt_template = """
You are a helpful assistant that extracts structured data from web pages.
You will be given a web page and you need to extract the following information:
{content}

schema: {schema}
Please provide the extracted data in JSON format.
WITH ONLY THE FIELDS THAT ARE IN THE SCHEMA.
"""

In [5]:
classification_prompt_template = """
{
  "title": {"type": "string", "description": "Page title"},
  "price": {"type": "number", "description": "Product price"},
  "description": {"type": "string", "description": "Product description"}
}
"""

In [6]:
# classification_prompt_template = """
#     # HTML Chunk Relevance Classification Prompt

#     You are an HTML content classifier. Your task is to analyze an HTML chunk against a given schema and determine if the content is relevant.

#     ## Instructions:
#     1. Carefully examine the provided HTML chunk
#     2. Compare it against the given schema/criteria
#     3. Determine if the HTML chunk contains content that matches or is relevant to the schema
#     4. Respond with ONLY a JSON object containing a single field "relevant" with value 1 (relevant) or 0 (not relevant)

#     ## Input Format:
#     **Schema/Criteria:**
#     {schema}

#     **HTML Chunk:**
#     ```html
#     {content}
#     ```

#     ## Output Format:
#     Your response must be ONLY a valid JSON object with no additional text:

#     ```json
#     {{
#     "relevant": 1
#     }}
#     ```

#     OR

#     ```json
#     {{
#     "relevant": 0
#     }}
#     ```

#     ## Classification Rules:
#     - Output 1 if the HTML chunk contains content that matches the schema criteria
#     - Output 0 if the HTML chunk does not contain relevant content
#     - Consider semantic meaning, not just exact keyword matches
#     - Look at text content, attributes, structure, and context
#     - Ignore purely structural HTML elements (like divs, spans) unless they contain relevant content
#     - Be STRICT in your evaluation - only mark as relevant (1) if there is clear, meaningful content that directly relates to the schema
#     - Empty elements, placeholder text, navigation menus, headers/footers, and generic UI components should typically be marked as not relevant (0)
#     - The HTML chunk does not need to contain ALL schema information, but it must contain SUBSTANTIAL and SPECIFIC content related to the schema

#     CRITICAL: Your entire response MUST be exactly one JSON object. DO NOT include any explanations, reasoning, markdown formatting, code blocks, or additional text. Output ONLY the raw JSON object.
#     """

In [7]:
pre = BasicPreprocessor(config={'keep_tags':True})
# llm = GeminiLLMClient(config={'api_key': os.getenv('GEMINI_API_KEY'),})
# ai = AIExtractor(llm_client=llm ,prompt_template=prompt_template)
ai = LLMClassifierExtractor(reranker=reranker, llm_client=llm, prompt_template=prompt_template, classifier_prompt=classification_prompt_template)
post = PostProcessor()

In [41]:
html_chunks = [
    """
    <div class="product-card">
        <h2 class="product-title">Wireless Noise Cancelling Headphones</h2>
        <p class="product-description">Experience immersive sound with active noise cancellation and long battery life.</p>
        <span class="price">$299.99</span>
        <button>Add to Cart</button>
    </div>
    """,

    """
    <section class="blog-post">
        <h1>Top 5 AI Tools to Try in 2025</h1>
        <p>Artificial intelligence continues to evolve. Here are five tools you should explore in 2025:</p>
        <ul>
            <li>LangChain</li>
            <li>AutoGen</li>
            <li>OpenDevin</li>
            <li>FastRAG</li>
            <li>GPTScript</li>
        </ul>
        <footer>Published by <strong>TechToday</strong> on June 30, 2025</footer>
    </section>
    """,

    """
    <section class="blog-post">
        <h1>Top 5 AI Tools to Try in 2025</h1>
        <p>Artificial intelligence continues to evolve. Here are five tools you should explore in 2025:</p>
        <ul>
            <li>LangChain</li>
            <li>AutoGen</li>
            <li>OpenDevin</li>
            <li>FastRAG</li>
            <li>GPTScript</li>
        </ul>
        <footer>Published by <strong>TechToday</strong> on June 30, 2025</footer>
    </section>
    """,

    """
    شسيمنبتشسينبتشسكنميبتكشسمينتبك
    """
]


In [42]:
len(html_chunks)

4

In [12]:
output = reranker.rerank(query=classification_prompt_template,passages=html_chunks, threshold=0)

Bonjour
<class 'list'> [Document(metadata={}, page_content='\n    <div class="product-card">\n        <h2 class="product-title">Wireless Noise Cancelling Headphones</h2>\n        <p class="product-description">Experience immersive sound with active noise cancellation and long battery life.</p>\n        <span class="price">$299.99</span>\n        <button>Add to Cart</button>\n    </div>\n    '), Document(metadata={}, page_content='\n    <section class="blog-post">\n        <h1>Top 5 AI Tools to Try in 2025</h1>\n        <p>Artificial intelligence continues to evolve. Here are five tools you should explore in 2025:</p>\n        <ul>\n            <li>LangChain</li>\n            <li>AutoGen</li>\n            <li>OpenDevin</li>\n            <li>FastRAG</li>\n            <li>GPTScript</li>\n        </ul>\n        <footer>Published by <strong>TechToday</strong> on June 30, 2025</footer>\n    </section>\n    '), Document(metadata={}, page_content='\n    <section class="blog-post">\n        <h1

In [ ]:
for o in output:
    print(o)
    print('-'*80)

page_content='
    <div class="product-card">
        <h2 class="product-title">Wireless Noise Cancelling Headphones</h2>
        <p class="product-description">Experience immersive sound with active noise cancellation and long battery life.</p>
        <span class="price">$299.99</span>
        <button>Add to Cart</button>
    </div>
    ' metadata={'relevance_score': -11.25, 'softmax_score': 0.9546922134634852, 'minmax_score': 1.0}
--------------------------------------------------------------------------------
page_content='
    <section class="blog-post">
        <h1>Top 5 AI Tools to Try in 2025</h1>
        <p>Artificial intelligence continues to evolve. Here are five tools you should explore in 2025:</p>
        <ul>
            <li>LangChain</li>
            <li>AutoGen</li>
            <li>OpenDevin</li>
            <li>FastRAG</li>
            <li>GPTScript</li>
        </ul>
        <footer>Published by <strong>TechToday</strong> on June 30, 2025</footer>
    </section>
    

In [14]:
len(output)

4

In [15]:
# ai.extract(chunks=["the price is $1000", "the title is 'NVIDIA H100 SXM'"])

In [17]:
pipe = Pipeline(preprocessor=pre, ai_extractor=ai, postprocessor=post)

In [18]:
from pydantic import BaseModel, Field, constr, condecimal

class ProductModel(BaseModel):
    productTitle: constr(min_length=1, max_length=200) = Field(
        ...,
        title="Product Title",
        description="The full title of the product"
    )
    price: condecimal(gt=0, decimal_places=2) = Field(
        ...,
        title="Product Price",
        description="Unit price (must be > 0, two decimal places)."
    )
    manufacturer: constr(min_length=1, max_length=1000) = Field(
        ...,
        title="Manufacturer",
        description="Name of the product manufacturer."
    )

    

In [19]:
config = {
    'keep_tags': True,
}

In [20]:
# url = "https://www.amazon.com/Instant-Pot-Multi-Use-Programmable-Pressure/dp/B00FLYWNYQ?_encoding=UTF8&content-id=amzn1.sym.2f889ce0-246f-467a-a086-d9a721167240&dib=eyJ2IjoiMSJ9.2EzBddTDEktLY8ckTsraM_cZ6pzKuNkA6y_gLR0-Uz1ekttQU6tuQEcjb8PThy0PfhvxLqeYWh3N7pQrGgRxAWzapVklC_aU6xBzD-3Wwqx3qyQRHsmOhPRsSpeCOIIZqS3SKDowZEPYrGnCbRMt5vxnsYMW-fD-zBbgeoeGYmbsN2U6_HNhLjrpePKCbQPmnZBJ9UhgYE4fE3DVuYm8xlJe9l5GixDLVFtZUq4m5FE.Ol-jiuu9P6mQie0yXLJj-Ht5-TXmIXuRPije85p_YVo&dib_tag=se&keywords=cooker&pd_rd_r=2cede598-f3ae-49ca-8a46-e5945a9c2631&pd_rd_w=2HLSC&pd_rd_wg=ZyUUn&qid=1749508157&sr=8-3"
schema = ProductModel  # pydantic class


# read html file 
with open(r'C:\Users\abdfa\Desktop\UNI STUFFING\GRADUATION PROJECT\Group Work\Experimental\data\tmp\SWDE-Camera\files\camera-amazon(1767)\0000.htm', 'r', encoding='utf-8') as file:
    content = file.read()

# with open(r'C:\Users\abdfa\Desktop\UNI STUFFING\GRADUATION PROJECT\Group Work\MCP_WEB2JSON\Amazon.com_ Instant Pot Duo 7-in-1 Electric Pressure Cooker, Slow Cooker, Rice Cooker, Steamer, Sauté, Yogurt Maker, Warmer & Sterilizer, Includes App With Over 800 Recipes, Stainless Steel, 6 Quart.htm', 'r', encoding='utf-8') as file:
#     content = file.read()


In [18]:
# import os

# content = """<html>
# <body>
# """

# from web2json.ai_extractor import HFRerankerClient, LLMClassifierExtractor, NvidiaLLMClient

# hf_reranker = HFRerankerClient()
# llm_client = NvidiaLLMClient(config={"api_key": os.environ.get('NVIDIA_API_KEY')})
# extractor = LLMClassifierExtractor(
#     reranker=hf_reranker,
#     llm_client=llm_client,
#     prompt_template="Extract from: {content} using schema: {schema}",
#     classifier_prompt="What is the price?"
# )

# # Run using HuggingFace reranker
# result = extractor.extract(content=content, schema=schema, hf=True)


In [21]:
# pipe.run(content=url,is_url=True, schema=schema, hf=False)

In [22]:
content

'\ufeff<base href="http://www.amazon.com/gp/product/tech-data/B0035FZJKI"/>\n\n    \n\n    \n    \n    \n\n  \n  \n    \n \n\n\n\n\n\n\n\n\n\n\n    \n    \n    \n\n\n\n\n\n\n    \n\n\n\n\n\n\n\n\n  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n    \n\n\n\n\n\n\n\n\n  \n  \n  \n    \n    \n\n\n\n\n\n<html>\n<head>\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n<style type="text/css"><!--\n\n\n\n\n\nBODY { font-family: verdana,arial,helvetica,sans-serif; font-size: small; background-color: #FFFFFF; color: #000000; margin-top: 0px; }\nTD, TH { font-family: verdana,arial,helvetica,sans-serif; font-size: small; }\n\n\n.serif { font-family: times,serif; font-size: medium; }\n.sans { font-family: verdana,arial,helvetica,sans-serif; font-size: medium; }\n\n.small { font-family: verdana,arial,helvetica,sans-serif; font-size: small; }\n\n.h1 { font-family: verdana,arial,helvetica,sans-serif; color: #E47911; font-size: medium; }\n.h3color { font-family: verdana,arial,helvetica,sans-serif; color: #E47911; font-size

In [ ]:
import torch 

softmax_scores = [0.6 , 0.3 , 0.06 , 0.01]
softmax_scores = torch.tensor(softmax_scores)
softmax_scores = softmax_scores / softmax_scores.sum()

# Normalize to [0, 1]
softmax_scores = (softmax_scores - softmax_scores.min()) / (softmax_scores.max() - softmax_scores.min())
softmax_scores

tensor([0., 0., 1.])

In [25]:
chunks = ai.chunk_content(content=content)

ERROR	Property: Invalid value for "CSS Level 2.1" property: expression(this.scrollHeight > 183?"184px": "auto") [260:7: height]
ERROR	Property: Invalid value for "CSS3 Basic User Interface Module" property: hand [445:3: cursor]
ERROR	Selector: Unexpected IDENT. [461:2: html]
ERROR	SelectorList: Invalid Selector: *html div.mbcTradeIn
WARNING	Property: Unknown Property name. [489:9: -moz-border-radius-topright]
WARNING	Property: Unknown Property name. [490:9: -moz-border-radius-bottomright]
WARNING	Property: Unknown Property name. [491:9: -webkit-border-top-right-radius]
WARNING	Property: Unknown Property name. [492:9: -webkit-border-bottom-right-radius]
WARNING	Property: Unknown Property name. [506:9: -moz-box-shadow]
WARNING	Property: Unknown Property name. [516:9: text-size]
ERROR	PropertyValue: No match: ('CHAR', ':', 518, 15)
ERROR	PropertyValue: Unknown syntax or no value:  center
        cursor: pointer
ERROR	CSSStyleDeclaration: Syntax Error in Property: text-align: center
      

2


ERROR	Property: Invalid value for "CSS Level 2.1" property: expression(this.scrollHeight > 183?"184px": "auto") [260:7: height]
ERROR	Property: Invalid value for "CSS3 Basic User Interface Module" property: hand [445:3: cursor]
ERROR	Selector: Unexpected IDENT. [461:2: html]
ERROR	SelectorList: Invalid Selector: *html div.mbcTradeIn
WARNING	Property: Unknown Property name. [489:9: -moz-border-radius-topright]
WARNING	Property: Unknown Property name. [490:9: -moz-border-radius-bottomright]
WARNING	Property: Unknown Property name. [491:9: -webkit-border-top-right-radius]
WARNING	Property: Unknown Property name. [492:9: -webkit-border-bottom-right-radius]
WARNING	Property: Unknown Property name. [506:9: -moz-box-shadow]
WARNING	Property: Unknown Property name. [516:9: text-size]
ERROR	PropertyValue: No match: ('CHAR', ':', 518, 15)
ERROR	PropertyValue: Unknown syntax or no value:  center
        cursor: pointer
ERROR	CSSStyleDeclaration: Syntax Error in Property: text-align: center
      

In [26]:
len(chunks)

41

In [29]:
chunks

['<html><head><base href="http:..."/><link href="http:..." rel="stylesheet" type="text/css"/><noscript><link href="http:..." rel="stylesheet" type="text/css"/></noscript><meta content="text/html; charset=utf-8" http-equiv="content-type"/><link href="http:..." rel="canonical"/><meta content="Amazon.com: Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver): Camera &amp; Photo" name="description"/><meta content="Amazon.com: Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver): Camera &amp; Photo" name="title"/><meta content="Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver),Canon,SD1300IS Silver" name="keywords"/><title>Amazon.com: Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver): Camera &amp; Photo</ti

In [39]:
output = reranker.rerank(query=classification_prompt_template,passages=chunks, threshold=-1)

Bonjour
<class 'list'> [Document(metadata={}, page_content='<html><head><base href="http:..."/><link href="http:..." rel="stylesheet" type="text/css"/><noscript><link href="http:..." rel="stylesheet" type="text/css"/></noscript><meta content="text/html; charset=utf-8" http-equiv="content-type"/><link href="http:..." rel="canonical"/><meta content="Amazon.com: Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver): Camera &amp; Photo" name="description"/><meta content="Amazon.com: Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver): Camera &amp; Photo" name="title"/><meta content="Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver),Canon,SD1300IS Silver" name="keywords"/><title>Amazon.com: Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabili

In [40]:
output

[Document(metadata={'relevance_score': -14.578125, 'softmax_score': 0.29085356753038766, 'minmax_score': 1.0}, page_content='<html><body class="dp"><div class="singlecolumnminwidth" id="divsinglecolumnminwidth"><form action="http://www.amazon.com/gp/product/handle-buy-box/ref=dp_start-bbf_1_tech-data" id="handleBuy" method="post" name="handleBuy" style="margin: 0pt;"><table border="0" cellpadding="0" cellspacing="0"><tr><td valign="top" width="100%"><div id="price-and-olp-condition-link-outer"><div id="price-and-olp-condition-link-inner"><div id="price_feature_div">\n<div id="price_inner_div">\n<div class="buying" id="priceBlock">\n<table class="product">\n<tr>\n<td class="priceBlockLabel">List Price:</td>\n<td><span class="listprice">$179.99</span></td>\n</tr>\n<tr>\n<td class="priceBlockLabelPrice">Price:</td>\n<td><b class="priceLarge">$129.00</b> \n      \n\n      \n\n\n\n\n    \n    \n\n\n\n\n\n\n\n\n\n\n&amp; this item ships for <b>FREE with Super Saver Shipping</b>.\n\n\n\n<a hr

In [31]:
output

[Document(metadata={'relevance_score': -16.578125, 'softmax_score': 0.9005297861178929, 'minmax_score': 1.0}, page_content='<html><head><base href="http:..."/><link href="http:..." rel="stylesheet" type="text/css"/><noscript><link href="http:..." rel="stylesheet" type="text/css"/></noscript><meta content="text/html; charset=utf-8" http-equiv="content-type"/><link href="http:..." rel="canonical"/><meta content="Amazon.com: Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver): Camera &amp; Photo" name="description"/><meta content="Amazon.com: Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver): Camera &amp; Photo" name="title"/><meta content="Canon PowerShot SD1300 IS 12.1 MP Digital Camera with 4x Wide Angle Optical Image Stabilized Zoom and 2.7-Inch LCD (Silver),Canon,SD1300IS Silver" name="keywords"/><title>Amazon.com: Canon PowerShot SD1300 IS